# Create Hello World Scatterplot

In [2]:
import pandas as pd
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
# Load the CSV file into a DataFrame
df = pd.read_csv("../data/cleaned_businessV2.csv")

# Display the first few rows to confirm it's loaded correctly
#df.head()

# Convert float column to int column
#df["stars"] = df["stars"].astype(int)
#df.dtypes
#df.head()


In [4]:
output_notebook()

# Create a figure
p = figure(title="Data from CSV", x_axis_label="X values", y_axis_label="Y values")

# Add a line or scatter plot using the data from ColumnDataSource
#p.line('x', 'y', source=source, legend_label="Line", line_width=2)
# or for a scatter plot:
p.circle('stars', 'review_count', source=df, size=5, color="navy", alpha=0.5)

# Show the plot
show(p)


Loading BokehJS ...

# Plot with Widget Experiment

In [10]:
import pandas as pd
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource
from bokeh.layouts import column
from bokeh.models.widgets import Slider, Select
from bokeh.layouts import row
from bokeh.events import ButtonClick
from bokeh.models.widgets import Button
from bokeh.models import CustomJS, CheckboxGroup

In [12]:
# Load the data (replace 'path/to/your/file.csv' with the actual path)
data = pd.read_csv("../data/cleaned_businessV2.csv")
source = ColumnDataSource(data)

In [13]:
# Initialize a figure
p = figure(title="Interactive Filtered Data Plot", x_axis_label="X", y_axis_label="Y")
p.circle('x', 'y', source=source, size=8, color="navy", alpha=0.5)


GlyphRenderer(id='p1180', ...)

In [15]:
# Add filtering widget
slider = Slider(start=data['stars'].min(), end=data['stars'].max(), value=data['stars'].min(), step=1, title="X-Value Filter")


In [17]:
# Dropdown for categorical data
category_options = list(data['hours_Monday'].unique())  # replace 'category_column' with actual column name
dropdown = Select(title="Category", value=category_options[0], options=category_options)


In [18]:
# Checkbox for multi-select categories
checkboxes = CheckboxGroup(labels=category_options, active=[])


In [43]:
# Add Callback Functions
from bokeh.models import CustomJS

# Update the data source based on slider and dropdown selections
callback = CustomJS(args=dict(source=source, original_data=source.data, slider=slider, dropdown=dropdown), code="""
    const data = source.data;
    const original = original_data;
    const x = data['x'];
    const y = data['y'];
    const category = data['category_column'];  // replace 'category_column' with actual column name

    const selected_x = slider.value;
    const selected_category = dropdown.value;

    // Filter the data
    for (let i = 0; i < x.length; i++) {
        if (original['x'][i] >= selected_x && original['category_column'][i] == selected_category) {
            x[i] = original['x'][i];
            y[i] = original['y'][i];
        } else {
            x[i] = null;
            y[i] = null;
        }
    }
    source.change.emit();
""")

# Attach the callback to widgets
slider.js_on_change('value', callback)
dropdown.js_on_change('value', callback)


NameError: name 'slider' is not defined

In [21]:
# Layout and Display
layout = column(p, slider, dropdown)
show(layout)


ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name. This could either be due to a misspelling or typo, or due to an expected column being missing. : x='x' [no close matches], y='y' [no close matches] {renderer: GlyphRenderer(id='p1180', ...)}


# Create Line with Javascript Experiment

## Triangular Model Prototype with on-click appearance of lines (Created by ChatGPT)

In [ ]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, CustomJS, TapTool
from bokeh.io import output_notebook
from bokeh.models import DatetimeTickFormatter, Range1d
import pandas as pd
from datetime import datetime, timedelta

output_notebook()

# Sample data for scatter plot
scatter_data = ColumnDataSource(data={
    'x': [datetime(2024, 11, 1, hour=1), datetime(2024, 11, 1, hour=2), datetime(2024, 11, 1, hour=3),
          datetime(2024, 11, 1, hour=4), datetime(2024, 11, 1, hour=5)],
    'y': [5, 4, 3, 2, 1]
})

# Empty data for the combined click line
line_data = ColumnDataSource(data={'x': [], 'y': []})

# Create figure
p = figure(title="Scatter Plot with Click-to-Show Line", tools="tap,pan,wheel_zoom,box_zoom,reset",
           x_axis_label="Time of Day", y_axis_label="Y", x_axis_type='datetime')

# Set x-axis range to start at 00:00
p.x_range = Range1d(start=datetime(2024, 11, 1, hour=0), end=datetime(2024, 11, 1, hour=23))
p.y_range = Range1d(start=0, end=24)

# Set x-axis format to HH:MM
p.xaxis.formatter = DatetimeTickFormatter(hours='%H:%M', minutes='%H:%M')

# Scatter plot
p.circle('x', 'y', size=10, color="navy", alpha=0.5, source=scatter_data)

# Line plot (initially empty)
line = p.line('x', 'y', line_width=2, color="red", source=line_data)

# JavaScript callback to display a line when clicking on a point
click_callback = CustomJS(args=dict(scatter_data=scatter_data, line_data=line_data), code="""
    // Get the selected point index
    const indices = scatter_data.selected.indices;
    
    if (indices.length > 0) {
        // If a point is clicked, get its coordinates
        const index = indices[0];
        const x_click = scatter_data.data['x'][index];
        const y_click = scatter_data.data['y'][index];
        
        // Define coordinates for the combined line
        const x_values = [x_click - 3600000, x_click, x_click + 3600000]; // 1 hour before and after in milliseconds
        const y_values = [0, y_click, 0];
        
        // Update line_data source with new line coordinates
        line_data.data = {x: x_values, y: y_values};
        line_data.change.emit();
    }
""")

# Add TapTool and link it with the callback
tap_tool = p.select(type=TapTool)
tap_tool.callback = click_callback

# Show plot
show(p)


Loading BokehJS ...